In [3]:
import pandas as pd
import geopandas as gpd

# Notes:
This notebook depends on the sa2 population.

Serve like a playground to help merge real estate data with population, income and distance 

In [ ]:
#Load all relevant datasets


LANDING_DATA_DIR = "../../data/landing"
RAW_DATA_DIR = "../../data/raw"
CURATED_DATA_DIR = "../../data/curated"

population = pd.read_csv(f"{CURATED_DATA_DIR}/population.csv")
income = pd.read_csv(f"{CURATED_DATA_DIR}/income.csv")
real_estate = gpd.read_file(f"{CURATED_DATA_DIR}/real_estate_2023.csv")
postcode = gpd.read_file(
    f"{LANDING_DATA_DIR}/postcodes/ll_gda2020/esrishape/whole_of_dataset/victoria/VMLITE")
sa2 = gpd.read_file(f"{RAW_DATA_DIR}/sa2")
suburb = gpd.read_file(f"{LANDING_DATA_DIR}/suburb_locations/GDA2020")


In [ ]:
real_estate = real_estate.drop(['field_1', 'geometry'], axis=1)

In [57]:
tally = 0
for idx, row in real_estate.iterrows():
    if isinstance(row['coordinates'], list):
        print(idx)
        tally += 1
print(tally)

0


In [59]:
for idx, row in real_estate.iterrows():
    lat_lon = row['coordinates'].strip('[]').split(', ')
    temp = []
    for num in lat_lon:
        temp.append(float(num))
    row['coordinates'] = temp
    

Finding straight distance to cbd for each property.

In [61]:
#Loading Phoebe's PTV data
ptv_stops = gpd.read_file(f"{RAW_DATA_DIR}/ptv/metro_trains_stops.shp")

ptv_stops

stop_id                                    stop_name   stop_lat  \
0      15351            Sunbury Railway Station (Sunbury) -37.579091   
1      15353  Diggers Rest Railway Station (Diggers Rest) -37.627017   
2      19827     Stony Point Railway Station (Crib Point) -38.374235   
3      19828      Crib Point Railway Station (Crib Point) -38.366123   
4      19829        Morradoo Railway Station (Crib Point) -38.354033   
..       ...                                          ...        ...   
216    49343          Union Railway Station (Mont Albert) -37.823118   
217    52095       Southland Railway Station (Cheltenham) -37.958756   
218    52159  Middle Gorge Railway Station (South Morang) -37.644061   
219    52160     Hawkstowe Railway Station (South Morang) -37.622995   
220    52161              Mernda Railway Station (Mernda) -37.602548   

       stop_lon                     geometry  
0    144.727319  POINT (144.72732 -37.57909)  
1    144.719922  POINT (144.71992 -37.62702)  
2    145.221837  POINT (145.22184 -38.37423)  
3    145.204043  POINT (145.20404 -38.36612)  
4    145.189602  POINT (145.18960 -38.35403)  
..          ...                          ...  
216  145.100278  POINT (145.10028 -37.82312)  
217  145.049121  POINT (145.04912 -37.95876)  
218  145.092144  POINT (145.09214 -37.64406)  
219  145.097396  POINT (145.09740 -37.62299)  
220  145.100885  POINT (145.10088 -37.60255)  

[221 rows x 5 columns]

In [62]:
#Finding Melbourne Central Station. Index 17.
search_word = 'Melbourne'
result = ptv_stops[ptv_stops['stop_name'].str.contains(search_word, case=False)]
result

stop_id                                          stop_name   stop_lat  \
16     19841         Flagstaff Railway Station (Melbourne City) -37.811981   
17     19842  Melbourne Central Railway Station (Melbourne C... -37.809939   
18     19843        Parliament Railway Station (Melbourne City) -37.811054   
29     19854   Flinders Street Railway Station (Melbourne City) -37.818305   
144    19971  Flemington Bridge Railway Station (North Melbo... -37.788140   
145    19972         Macaulay Railway Station (North Melbourne) -37.794267   
146    19973   North Melbourne Railway Station (West Melbourne) -37.807419   
152    19979      Jolimont-MCG Railway Station (East Melbourne) -37.816527   
208    22180    Southern Cross Railway Station (Melbourne City) -37.817936   

       stop_lon                     geometry  
16   144.955654  POINT (144.95565 -37.81198)  
17   144.962594  POINT (144.96259 -37.80994)  
18   144.972911  POINT (144.97291 -37.81105)  
29   144.966964  POINT (144.96696 -37.81831)  
144  144.939323  POINT (144.93932 -37.78814)  
145  144.936166  POINT (144.93617 -37.79427)  
146  144.942570  POINT (144.94257 -37.80742)  
152  144.984098  POINT (144.98410 -37.81653)  
208  144.951411  POINT (144.95141 -37.81794)

In [63]:
#Getting distance between 2 points in kilometers. Let Melbourne Central PTV station coordinates represent CBD.
from geopy import distance
mc_coord = (ptv_stops['geometry'][17].y, ptv_stops['geometry'][17].x)

def distance_to_cbd(coords):
    return distance.distance(mc_coord, coords).km

real_estate['distance_to_cbd'] = real_estate['coordinates'].apply(distance_to_cbd)

Merging the relevant datasets

In [68]:
real_estate

coordinates            property_type  \
0              [-37.8095116, 144.9691204]  Apartment / Unit / Flat   
1              [-37.8170971, 144.9601487]  Apartment / Unit / Flat   
2               [-37.816228, 144.9532465]  Apartment / Unit / Flat   
3              [-37.8147259, 144.9621291]  Apartment / Unit / Flat   
4               [-37.8096052, 144.962371]                    House   
...                                   ...                      ...   
11655          [-38.6393294, 145.7151855]                    House   
11656          [-38.6322823, 145.7076844]                    House   
11657  [-38.629970900000004, 145.7098975]                    House   
11658          [-38.6327098, 145.7232642]                    House   
11659          [-38.6339662, 145.7253717]                Townhouse   

      price_per_week postcode parking_spaces bedrooms bathrooms  \
0              850.0     3000            1.0      2.0       2.0   
1              475.0     3000                     1.0       1.0   
2              630.0     3000            1.0      2.0       1.0   
3              450.0     3000                     1.0       1.0   
4              900.0     3000            2.0      2.0       1.0   
...              ...      ...            ...      ...       ...   
11655          410.0     3996            1.0      2.0       1.0   
11656          470.0     3996            1.0      3.0       1.0   
11657          600.0     3996            2.0      3.0       2.0   
11658          410.0     3996                     3.0       1.0   
11659          450.0     3996            1.0      3.0       2.0   

      furnished_found  distance_to_cbd  
0               False         0.576701  
1                True         0.823173  
2               False         1.079214  
3               False         0.532909  
4                True         0.041890  
...               ...              ...  
11655            True       113.217230  
11656            True       112.200691  
11657           False       112.105665  
11658           False       113.037672  
11659           False       113.258778  

[11660 rows x 9 columns]

In [120]:
from shapely.geometry import Point
sa2_polygons = gpd.GeoDataFrame(sa2)
real_estate['sa2_name'] = None
null_tally = 0
for idx, row in real_estate.iterrows():
    point = Point(row['coordinates'][1], row['coordinates'][0])
    result = sa2_polygons[sa2_polygons.geometry.contains(point)]
    if not result.empty:
        real_estate['sa2_name'][idx] = result.values[0][0]
    else:
        real_estate['sa2_name'][idx] = "Null"
        null_tally += 1

/tmp/ipykernel_559/1989955473.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  real_estate['sa2_name'][idx] = result.values[0][0]
/tmp/ipykernel_559/1989955473.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  real_estate['sa2_name'][idx] = result.values[0][0]
/tmp/ipykernel_559/1989955473.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  real_estate['sa2_name'][idx] = result.values[0][0]
/tmp/ipykernel_559/1989955473.py:9: Sett

In [121]:
print(null_tally)

9


In [126]:
real_estate = real_estate.drop("sa2", axis=1)

In [161]:
income = income.rename(columns={"SA2 NAME":"sa2_name"})

In [162]:
income_2019 = income[income['Year'] == 2019]

In [163]:
real_estate2 = real_estate.merge(income_2019, on="sa2_name", how='left').drop(columns=["Year", "SA2"])
real_estate2

coordinates            property_type  \
0              [-37.8095116, 144.9691204]  Apartment / Unit / Flat   
1              [-37.8170971, 144.9601487]  Apartment / Unit / Flat   
2               [-37.816228, 144.9532465]  Apartment / Unit / Flat   
3              [-37.8147259, 144.9621291]  Apartment / Unit / Flat   
4               [-37.8096052, 144.962371]                    House   
...                                   ...                      ...   
11655          [-38.6393294, 145.7151855]                    House   
11656          [-38.6322823, 145.7076844]                    House   
11657  [-38.629970900000004, 145.7098975]                    House   
11658          [-38.6327098, 145.7232642]                    House   
11659          [-38.6339662, 145.7253717]                Townhouse   

      price_per_week postcode parking_spaces bedrooms bathrooms  \
0              850.0     3000            1.0      2.0       2.0   
1              475.0     3000                     1.0       1.0   
2              630.0     3000            1.0      2.0       1.0   
3              450.0     3000                     1.0       1.0   
4              900.0     3000            2.0      2.0       1.0   
...              ...      ...            ...      ...       ...   
11655          410.0     3996            1.0      2.0       1.0   
11656          470.0     3996            1.0      3.0       1.0   
11657          600.0     3996            2.0      3.0       2.0   
11658          410.0     3996                     3.0       1.0   
11659          450.0     3996            1.0      3.0       2.0   

      furnished_found  distance_to_cbd               sa2_name  Median Income  
0               False         0.576701   Melbourne CBD - East            NaN  
1                True         0.823173   Melbourne CBD - West            NaN  
2               False         1.079214   Melbourne CBD - West            NaN  
3               False         0.532909   Melbourne CBD - West            NaN  
4                True         0.041890  Melbourne CBD - North            NaN  
...               ...              ...                    ...            ...  
11655            True       113.217230  Wonthaggi - Inverloch        41773.0  
11656            True       112.200691  Wonthaggi - Inverloch        41773.0  
11657           False       112.105665  Wonthaggi - Inverloch        41773.0  
11658           False       113.037672  Wonthaggi - Inverloch        41773.0  
11659           False       113.258778  Wonthaggi - Inverloch        41773.0  

[11660 rows x 11 columns]

In [182]:
from shapely.geometry import Point
suburb_polygons = gpd.GeoDataFrame(suburb)
real_estate2['suburb_name'] = None
null_tally = 0
for idx, row in real_estate2.iterrows():
    point = Point(row['coordinates'][1], row['coordinates'][0])
    result = suburb_polygons[suburb_polygons.geometry.contains(point)]
    if not result.empty:
        real_estate2['suburb_name'][idx] = result.values[0][3]
    else:
        real_estate2['suburb_name'][idx] = "Null"
        null_tally += 1

/tmp/ipykernel_559/234575559.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  real_estate2['suburb_name'][idx] = result.values[0][3]
/tmp/ipykernel_559/234575559.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  real_estate2['suburb_name'][idx] = result.values[0][3]
/tmp/ipykernel_559/234575559.py:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  real_estate2['suburb_name'][idx] = result.values[0][3]
/tmp/ipykernel_559/234575559.py

In [194]:
population_2022 = population[population['Year'] == 2022].rename(columns={"SA2 name":"sa2_name"}).drop(columns=["S/T name", "SA2 code", "Year"])

In [196]:
real_estate_final = real_estate2.merge(population_2022, on="sa2_name", how='left')
real_estate_final

coordinates            property_type  \
0              [-37.8095116, 144.9691204]  Apartment / Unit / Flat   
1              [-37.8170971, 144.9601487]  Apartment / Unit / Flat   
2               [-37.816228, 144.9532465]  Apartment / Unit / Flat   
3              [-37.8147259, 144.9621291]  Apartment / Unit / Flat   
4               [-37.8096052, 144.962371]                    House   
...                                   ...                      ...   
11655          [-38.6393294, 145.7151855]                    House   
11656          [-38.6322823, 145.7076844]                    House   
11657  [-38.629970900000004, 145.7098975]                    House   
11658          [-38.6327098, 145.7232642]                    House   
11659          [-38.6339662, 145.7253717]                Townhouse   

      price_per_week postcode parking_spaces bedrooms bathrooms  \
0              850.0     3000            1.0      2.0       2.0   
1              475.0     3000                     1.0       1.0   
2              630.0     3000            1.0      2.0       1.0   
3              450.0     3000                     1.0       1.0   
4              900.0     3000            2.0      2.0       1.0   
...              ...      ...            ...      ...       ...   
11655          410.0     3996            1.0      2.0       1.0   
11656          470.0     3996            1.0      3.0       1.0   
11657          600.0     3996            2.0      3.0       2.0   
11658          410.0     3996                     3.0       1.0   
11659          450.0     3996            1.0      3.0       2.0   

      furnished_found  distance_to_cbd               sa2_name  Median Income  \
0               False         0.576701   Melbourne CBD - East            NaN   
1                True         0.823173   Melbourne CBD - West            NaN   
2               False         1.079214   Melbourne CBD - West            NaN   
3               False         0.532909   Melbourne CBD - West            NaN   
4                True         0.041890  Melbourne CBD - North            NaN   
...               ...              ...                    ...            ...   
11655            True       113.217230  Wonthaggi - Inverloch        41773.0   
11656            True       112.200691  Wonthaggi - Inverloch        41773.0   
11657           False       112.105665  Wonthaggi - Inverloch        41773.0   
11658           False       113.037672  Wonthaggi - Inverloch        41773.0   
11659           False       113.258778  Wonthaggi - Inverloch        41773.0   

      suburb_name  Population  
0       Melbourne     10674.0  
1       Melbourne     17284.0  
2       Melbourne     17284.0  
3       Melbourne     17284.0  
4       Melbourne     18789.0  
...           ...         ...  
11655   Inverloch     27502.0  
11656   Inverloch     27502.0  
11657   Inverloch     27502.0  
11658   Inverloch     27502.0  
11659   Inverloch     27502.0  

[11660 rows x 13 columns]